# Exploratory Analysis of Violence Against Women and Girls (VAWG) Dataset
In this notebook I provide a basic quantitative and semantic analysis of the Violence Against Women and Girls dataset sourced from the [Demographic and Health Surveys](https://dhsprogram.com/methodology/Survey-Types/DHS.cfm) program, as well as support these analyses with some simple data visualization.

The original idea of what I wanted to do was look at time trends of domestic violence against women over time. It turns out that this particular dataset cannot be used to answer such a question. Will have to keep looking.

___
## Introduction

### About the dataset

### What is in this dataset?
Taken directly from the data_dictionary.pdf document included with the dataset - dtype column not included in data_dictionary.pdf

| Column Name | Description | dtype |
|---|---|---|
|RecordID|Numeric value unique to each question by country|int|
|Country|Country in which the survey was conducted|categorical|
|Gender|Whether the respondents were Male or Female|categorical|
|Demographics Question|Refers to the different types of demographic groupings used to segment respondents – marital status, education level, employment status, residence type, or age|categorical|
|Demographics Response|Refers to demographic segment into which the respondent falls (e.g. the age groupings are split into 15-24, 25-34, and 35-49)|categorical|
|Question|Respondents were asked if they agreed with the [statements listed below]|categorical|
|Survey Year|Year in which the Demographic and Health Survey (DHS) took place. “DHS surveys are nationally-representative household surveys that provide data for a wide range of monitoring and impact evaluation indicators in the areas of population, health, and nutrition. Standard DHS Surveys have large sample sizes (usually between 5,000 and 30,000 households) and typically are conducted around every 5 years, to allow comparisons over time.” (https://dhsprogram.com/What-We-Do/Survey-Types/ DHS.cfm)|date|
|Value|% of people surveyed in the relevant group who agree with the question (e.g. the percentage of women aged 15-24 in Afghanistan who agree that a husband is justified in hitting or beating his wife if she burns the food)|float|

Respondents were asked if they agreed with the following statements:
- A husband is justified in hitting or beating his wife if she burns the food 
- A husband is  justified in hitting or beating his wife if she argues with him  
- A husband is justified in hitting or beating his wife if she goes out without telling him 
- A husband is justified in hitting or beating his wife if she neglects the children  
- A husband is justified in hitting or beating his wife if she refuses to have sex with him  
- A husband is justified in hitting or beating his wife for at least one specific reason

___
### Loading the dataset and analysis of raw data

In [1]:
import altair as alt
import pandas as pd
import numpy as np
from IPython.display import display

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
# load in the data and take a look at categorical data

raw_data = pd.read_csv('data/violence_data.csv')
raw_data.describe(include='object')

Country Gender Demographics Question Demographics Response  \
count         12600  12600                 12600                 12600   
unique           70      2                     5                    15   
top     Afghanistan      F             Education         Never married   
freq            180   6300                  3360                   840   

                         Question Survey Year  
count                       12600       12600  
unique                          6          18  
top     ... if she burns the food  01/01/2013  
freq                         2100        1980

In [3]:
# take a look at the countries and years surveyed.

with pd.option_context('display.max_rows', None):
    display(raw_data.loc[:,['Country', 'Survey Year']].drop_duplicates().reset_index(drop=True))

Country Survey Year
0                 Afghanistan  01/01/2015
1                     Albania  01/01/2017
2                      Angola  01/01/2015
3                     Armenia  01/01/2015
4                  Azerbaijan  01/01/2006
5                  Bangladesh  01/01/2014
6                       Benin  01/01/2017
7                     Bolivia  01/01/2008
8                Burkina Faso  01/01/2010
9                     Burundi  01/01/2016
10                   Cambodia  01/01/2014
11                   Cameroon  01/01/2011
12                       Chad  01/01/2014
13                   Colombia  01/01/2015
14                    Comoros  01/01/2012
15                      Congo  01/01/2011
16  Congo Democratic Republic  01/01/2013
17              Cote d'Ivoire  01/01/2011
18         Dominican Republic  01/01/2013
19                      Egypt  01/01/2014
20                    Eritrea  01/01/2002
21                   Eswatini  01/01/2006
22                   Ethiopia  01/01/2016
23                      Gabon  01/01/2012
24                     Gambia  01/01/2013
25                      Ghana  01/01/2014
26                  Guatemala  01/01/2014
27                     Guinea  01/01/2018
28                     Guyana  01/01/2009
29                      Haiti  01/01/2016
30                   Honduras  01/01/2011
31                      India  01/01/2015
32                  Indonesia  01/01/2012
33                     Jordan  01/01/2017
34                      Kenya  01/01/2014
35            Kyrgyz Republic  01/01/2012
36                    Lesotho  01/01/2014
37                    Liberia  01/01/2013
38                 Madagascar  01/01/2008
39                     Malawi  01/01/2015
40                   Maldives  01/01/2016
41                       Mali  01/01/2018
42                    Moldova  01/01/2005
43                    Morocco  01/01/2003
44                 Mozambique  01/01/2015
45                    Myanmar  01/01/2015
46                    Namibia  01/01/2013
47                      Nepal  01/01/2016
48                  Nicaragua  01/01/2001
49                      Niger  01/01/2012
50                    Nigeria  01/01/2013
51                   Pakistan  01/01/2017
52                       Peru  01/01/2012
53                Philippines  01/01/2017
54                     Rwanda  01/01/2014
55      Sao Tome and Principe  01/01/2008
56                    Senegal  01/01/2017
57               Sierra Leone  01/01/2013
58               South Africa  01/01/2016
59                 Tajikistan  01/01/2017
60                   Tanzania  01/01/2015
61                Timor-Leste  01/01/2016
62                       Togo  01/01/2013
63                     Turkey  01/01/2013
64               Turkmenistan  01/01/2000
65                     Uganda  01/01/2016
66                    Ukraine  01/01/2007
67                      Yemen  01/01/2013
68                     Zambia  01/01/2013
69                   Zimbabwe  01/01/2015

So it looks like each country in which a survey has been conducted has only been surveyed a single time.

In [4]:
# for each year this survey has been conducted, let's
# take a look at the total number of surveys conducted,
# and the total number of countries in which the survey
# was conducted

survey_count = alt.Chart(raw_data).mark_bar().encode(
    x='Survey Year',
    y='count(RecordID)',
)

country_count = alt.Chart(raw_data).mark_bar().encode(
    x='Survey Year',
    y={"aggregate": "distinct",
       "field": "Country",
       "type": "quantitative"},
    tooltip=['Survey Year',
             'count(RecordID)',
             {"aggregate": "distinct",
              "field": "Country",
              "type": "quantitative"}]
)

alt.layer(survey_count, country_count).resolve_scale(
    y='independent',
)

alt.LayerChart(...)

Note the number of surveys conducted in each country is constant.

In [5]:
# let's check that distribution of participant gender makes sense

alt.Chart(raw_data).mark_bar().encode(
    x = 'count(RecordID)',
    y = 'Country',
    color = "Gender",
    tooltip = ['Survey Year', 'Gender', 'count(RecordID)']
).configure_axisX(orient='top')

alt.Chart(...)

In [6]:
print(raw_data.loc[:, ['Demographics Question',
                 'Demographics Response']
            ].drop_duplicates().sort_values('Demographics Question'))

alt.Chart(raw_data.sort_values('Demographics Question')).mark_bar().encode(
    alt.X('count(RecordID)'),
    alt.Y('Demographics Response',
          sort=alt.EncodingSortField(field="Demographics Question")),
    color="Gender",
    tooltip=["Demographics Question", "Demographics Response", "Gender", "count(RecordID)"],
).properties(width=100, height=160).facet("Country", columns=2).resolve_scale(y='independent',
                                                                               x='independent')

   Demographics Question         Demographics Response
6                    Age                         15-24
9                    Age                         25-34
12                   Age                         35-49
1              Education                        Higher
2              Education                     Secondary
3              Education                       Primary
13             Education                  No education
5             Employment             Employed for kind
7             Employment                    Unemployed
14            Employment             Employed for cash
0         Marital status                 Never married
4         Marital status  Widowed, divorced, separated
10        Marital status    Married or living together
8              Residence                         Rural
11             Residence                         Urban


alt.FacetChart(...)

### Conclusion - Follow-up Project Ideas